In [1]:
!pip install numpy -q

In [2]:
pip install lightning neurokit2 captum numpy pandas -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.9/44.9 kB 2.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 5.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 846.0/846.0 kB 19.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 708.4/708.4 kB 49.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 78.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 100.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 983.2/983.2 kB 58.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 849.5/849.5 kB 50.3 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
opencv-contrib-python 4.12.0.88 requires numpy<2.3.0,>=2; python_version >= "3.9", but you have numpy 1.26.4 which is incompatible.
pytensor 2.36.3 requires numpy>=2.0, but you have nu

In [1]:
import os, sys
import warnings; warnings.filterwarnings("ignore")
import pytorch_lightning; pytorch_lightning.seed_everything(22)

from tqdm import tqdm

import argparse
import random
import pandas as pd, numpy as np
import neurokit2 as nk
import torch
import torch.nn as nn, torch.optim as optim
import torch.nn.functional as F
import torch.nn.utils.prune as prune
import captum.attr as attr
import matplotlib.pyplot as pyplot
from keras.preprocessing.sequence import pad_sequences
from sklearn.metrics import f1_score
import pywt
import h5py


INFO:lightning_fabric.utilities.seed:Seed set to 22


In [ ]:
def thresholds_search(labels, preds):
    search_range = [round(t, 2) for t in np.arange(1, 20)*0.05]

    optimal_thresholds = []
    for cls in range(preds.shape[1]):
        f1_scores_cls = []
        for threshold in search_range:
            labels_cls, preds_cls = labels[:, cls], preds[:, cls]

            preds_cls = list(np.where(preds[:, cls] >= threshold, 1, 0))
            f1_scores_cls.append(f1_score(
                labels_cls, preds_cls
                , average = "macro"
            ))

        optimal_thresholds.append(search_range[np.argmax(f1_scores_cls)])

    return optimal_thresholds

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import os
import zipfile

# Define the path to the zip file in Google Drive
zip_file_path = '/content/drive/MyDrive/records.zip'

# Define the extraction path
extract_path = '/content'

# Create the extraction directory if it doesn't exist
os.makedirs(extract_path, exist_ok=True)

# Check if the zip file exists
if os.path.exists(zip_file_path):
    # Extract the zip file
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        zip_ref.extractall(extract_path)
    print(f"Successfully extracted {zip_file_path} to {extract_path}")
else:
    print(f"Error: {zip_file_path} not found.")

Mounted at /content/drive
Successfully extracted /content/drive/MyDrive/records.zip to /content


In [ ]:
# -------------------------
# utilities: filtering and peak detection
# -------------------------
def denoise(data):
    # wavelet transform
    coeffs = pywt.wavedec(data=data, wavelet='db5', level=9)
    cA9, cD9, cD8, cD7, cD6, cD5, cD4, cD3, cD2, cD1 = coeffs

    # Threshold denoising
    threshold = (np.median(np.abs(cD1)) / 0.6745) * (np.sqrt(2 * np.log(len(cD1))))
    cD1.fill(0)
    cD2.fill(0)
    for i in range(1, len(coeffs) - 2):
        coeffs[i] = pywt.threshold(coeffs[i], threshold)

    # Inverse wavelet transform to obtain the denoised signal
    rdata = pywt.waverec(coeffs=coeffs, wavelet='db5')
    return rdata


In [ ]:
PATH = "records"

# Lead order is I, II, III, aVR, aVL, aVF, V1, V2, V3, V4, V5, V6
SAMPLING_RATE = 500

metadata = pd.read_csv("metadata.csv")
codes = pd.read_csv("code.csv")

# Get the code -> mappnigs
code_mappings = codes[['Code', 'Category']]

# Convert to a dict
code_mappings = {str(key): value for (_, (key, value)) in code_mappings.iterrows()}

# Removes samples with more than 1 class
metadata = metadata[~metadata['AHA_Code'].str.contains(";")]

# Remove modifiers
metadata['AHA_Code'] = [code.split("+")[0] for code in metadata['AHA_Code']]

# Map AHA code to category
metadata['AHA_Code_Mapped'] = metadata['AHA_Code'].map(code_mappings)

In [ ]:
X = []
Y = []

for data in metadata.itertuples():
    ecg_data_path = os.path.join(PATH, data.ECG_ID + ".h5")

    ecg_data = h5py.File(ecg_data_path)

    ecg = ecg_data['ecg']

    # Take only
    ecg = ecg[:, :5000]

    denoised_ecg = np.array([denoise(lead) for lead in ecg])
    # denoised_ecg = denoised_ecg.transpose(1,0)
    X.append(np.array(denoised_ecg))
    Y.append(data.AHA_Code_Mapped)

X = np.array(X)
y = np.array(Y)
y = pd.get_dummies(Y, dtype=int).to_numpy()

print("Number of samples:", len(X))
print("Y shape (one-hot):", y.shape)
y = torch.tensor(np.array(y).argmax(axis=1), dtype=torch.long)

Number of samples: 22046
Y shape (one-hot): (22046, 11)


In [ ]:
X.shape

(22046, 12, 5000)

In [ ]:
from sklearn.model_selection import train_test_split
from torch.utils.data import TensorDataset, DataLoader

# ---- Stratified splitting ----
all_indices = list(range(len(X)))
all_labels = y  # label_idx for each sample

# First split: train+val (90%) vs test (10%)
trainval_indices, test_indices = train_test_split(
    all_indices,
    test_size=0.1,
    random_state=10,
    stratify=all_labels
)

trainval_labels = [all_labels[i] for i in trainval_indices]

# Second split: train (90% of trainval) vs val (10% of trainval)
train_indices, val_indices = train_test_split(
    trainval_indices,
    test_size=0.1,
    random_state=10,
    stratify=trainval_labels
)

print(np.array(X).shape, np.array(Y).shape)

# Create datasets
train_ds = TensorDataset(torch.Tensor(X[train_indices]), torch.Tensor(y[train_indices]))
val_ds = TensorDataset(torch.Tensor(X[val_indices]), torch.Tensor(y[val_indices]))
test_ds = TensorDataset(torch.Tensor(X[test_indices]), torch.Tensor(y[test_indices]))

train_loader = DataLoader(train_ds, batch_size=32, shuffle=True, drop_last=True)
val_loader = DataLoader(val_ds, batch_size=32, shuffle=False)
test_loader = DataLoader(test_ds, batch_size=32, shuffle=False)


(22046, 12, 5000) (22046,)


In [ ]:
y[2]

tensor(1)

In [2]:

class LightSEModule(nn.Module):
    def __init__(self,
        in_channels,
        reduction = 16,
    ):
        super(LightSEModule, self).__init__()
        self.pool = nn.AdaptiveAvgPool1d(1)

        self.s_conv = DSConv1d(
            in_channels, in_channels//reduction,
            kernel_size = 1,
        )
        self.act_fn = nn.ReLU()
        self.e_conv = DSConv1d(
            in_channels//reduction, in_channels,
            kernel_size = 1,
        )

    def forward(self,
        input,
    ):
        attention_scores = self.pool(input)

        attention_scores = self.s_conv(attention_scores)
        attention_scores = self.act_fn(attention_scores)
        attention_scores = self.e_conv(attention_scores)

        return input*torch.sigmoid(attention_scores)

class DSConv1d(nn.Module):
    def __init__(self,
        in_channels, out_channels,
        kernel_size, padding = 0, stride = 1,
    ):
        super(DSConv1d, self).__init__()
        self.dw_conv = nn.Conv1d(
            in_channels, in_channels,
            kernel_size = kernel_size, padding = padding, stride = stride,
            groups = in_channels,
            bias = False,
        )
        self.pw_conv = nn.Conv1d(
            in_channels, out_channels,
            kernel_size = 1,
            bias = False,
        )

    def forward(self,
        input,
    ):
        output = self.dw_conv(input)
        output = self.pw_conv(output)

        return output

class LightSEResBlock(nn.Module):
    def __init__(self,
        in_channels,
        downsample = False,
    ):
        super(LightSEResBlock, self).__init__()
        if downsample:
            self.out_channels = in_channels*2
            self.conv_1 = DSConv1d(
                in_channels, self.out_channels,
                kernel_size = 7, padding = 3, stride = 2,
            )
            self.identity = nn.Sequential(
                DSConv1d(
                    in_channels, self.out_channels,
                    kernel_size = 1, padding = 0, stride = 2,
                ),
                nn.BatchNorm1d(self.out_channels),
            )
        else:
            self.out_channels = in_channels
            self.conv_1 = DSConv1d(
                in_channels, self.out_channels,
                kernel_size = 7, padding = 3, stride = 1,
            )
            self.identity = nn.Identity()
        self.conv_2 = DSConv1d(
            self.out_channels, self.out_channels,
            kernel_size = 7, padding = 3, stride = 1,
        )

        self.convs = nn.Sequential(
            self.conv_1,
            nn.BatchNorm1d(self.out_channels),
            nn.ReLU(),
            nn.Dropout(0.3),
            self.conv_2,
            nn.BatchNorm1d(self.out_channels),
            LightSEModule(self.out_channels),
        )
        self.act_fn = nn.ReLU()

    def forward(self,
        input,
    ):
        output = self.convs(input) + self.identity(input)
        output = self.act_fn(output)

        return output

class LightSEResNet18(nn.Module):
    def __init__(self,
        base_channels = 64,
    ):
        super(LightSEResNet18, self).__init__()
        self.bblock = LightSEResBlock
        self.stem = nn.Sequential(
            nn.Conv1d(
                1, base_channels,
                kernel_size = 15, padding = 7, stride = 2,
            ),
            nn.BatchNorm1d(base_channels),
            nn.ReLU(),
            nn.MaxPool1d(
                kernel_size = 3, padding = 1, stride = 2,
            ),
        )
        self.stage_0 = nn.Sequential(
            self.bblock(base_channels),
            self.bblock(base_channels),
        )

        self.stage_1 = nn.Sequential(
            self.bblock(base_channels*1, downsample = True),
            self.bblock(base_channels*2),
        )
        self.stage_2 = nn.Sequential(
            self.bblock(base_channels*2, downsample = True),
            self.bblock(base_channels*4),
        )
        self.stage_3 = nn.Sequential(
            self.bblock(base_channels*4, downsample = True),
            self.bblock(base_channels*8),
        )

        self.pool = nn.AdaptiveAvgPool1d(1)

    def forward(self,
        input,
    ):
        output = self.stem(input)
        output = self.stage_0(output)

        output = self.stage_1(output)
        output = self.stage_2(output)
        output = self.stage_3(output)

        output = self.pool(output)

        return output

In [3]:

class LightX3ECG(nn.Module):
    def __init__(self,
        base_channels = 64,
        num_classes = 11,
    ):
        super(LightX3ECG, self).__init__()
        self.backbone_0 = LightSEResNet18(base_channels)
        self.backbone_1 = LightSEResNet18(base_channels)
        self.backbone_2 = LightSEResNet18(base_channels)
        self.lw_attention = nn.Sequential(
            nn.Linear(
                base_channels*24, base_channels*8,
            ),
            nn.BatchNorm1d(base_channels*8),
            nn.ReLU(),
            nn.Dropout(0.3),
            nn.Linear(
                base_channels*8, 3,
            ),
        )

        self.classifier = nn.Sequential(
            nn.Dropout(0.2),
            nn.Linear(
                base_channels*8, num_classes,
            ),
        )

    def forward(self,
        input,
        return_attention_scores = False,
    ):
        features_0 = self.backbone_0(input[:, 0, :].unsqueeze(1)).squeeze(2)
        features_1 = self.backbone_1(input[:, 1, :].unsqueeze(1)).squeeze(2)
        features_2 = self.backbone_2(input[:, 2, :].unsqueeze(1)).squeeze(2)
        attention_scores = torch.sigmoid(
            self.lw_attention(
                torch.cat(
                [
                    features_0,
                    features_1,
                    features_2,
                ],
                dim = 1,
                )
            )
        )
        merged_features = torch.sum(
            torch.stack(
            [
                features_0,
                features_1,
                features_2,
            ],
            dim = 1,
            )*attention_scores.unsqueeze(-1),
            dim = 1,
        )

        output = self.classifier(merged_features)

        if not return_attention_scores:
            return output
        else:
            return output, attention_scores

In [ ]:
from tqdm.notebook import tqdm
from sklearn.metrics import accuracy_score, precision_score, recall_score, roc_auc_score, f1_score

def train_fn(
    train_loaders,
    model,
    num_epochs,
    config,
    criterion,
    optimizer,
    scheduler = None,
    training_verbose = True,
):
    print("\nStart Training ...\n" + " = "*16)
    model = model.cuda()
    model = nn.DataParallel(model, device_ids = config["device_ids"])

    best_f1 = 0.0
    for epoch in tqdm(range(1, num_epochs + 1), disable = training_verbose):
        # if training_verbose:
          # print("epoch {:2}/{:2}".format(epoch, num_epochs) + "\n" + "-"*16)

        model.train()
        running_loss = 0.0
        running_labels, running_preds = [], []

        for ecgs, labels in tqdm(train_loaders["train"], disable = not training_verbose):
            ecgs, labels = ecgs.cuda(), labels.cuda()

            optimizer.zero_grad()
            logits = model(ecgs)
            loss = criterion(logits, labels)

            loss.backward()
            optimizer.step()

            running_loss = running_loss + loss.item()*ecgs.size(0)
            labels, preds = list(labels.data.cpu().numpy()), list(torch.max(logits, 1)[1].detach().cpu().numpy()) if not config["is_multilabel"] else list(np.where(torch.sigmoid(logits).detach().cpu().numpy() >= 0.50, 1, 0))
            running_labels.extend(labels), running_preds.extend(preds)

        if (scheduler is not None) and (not epoch > scheduler.T_max):
            scheduler.step()

        epoch_loss, epoch_f1 = running_loss/len(train_loaders["train"].dataset), f1_score(
            running_labels, running_preds
            , average = "weighted"
        )

        # if training_verbose:
            # print("{:<5} - loss:{:.4f}, f1:{:.4f}".format(
            #     "train",
            #     epoch_loss, epoch_f1
            # ))

        # Validation
        with torch.no_grad():
            model.eval()
            running_loss = 0.0
            running_labels, running_preds = [], []
            for ecgs, labels in tqdm(train_loaders["val"], disable = not training_verbose):
                ecgs, labels = ecgs.cuda(), labels.cuda()

                logits = model(ecgs)
                loss = criterion(logits, labels)

                running_loss = running_loss + loss.item()*ecgs.size(0)
                labels, preds = list(labels.data.cpu().numpy()), list(torch.max(logits, 1)[1].detach().cpu().numpy()) if not config["is_multilabel"] else list(np.where(torch.sigmoid(logits).detach().cpu().numpy() >= 0.50, 1, 0))
                running_labels.extend(labels), running_preds.extend(preds)

            val_epoch_loss, val_epoch_f1 = running_loss/len(train_loaders["val"].dataset), f1_score(
                running_labels, running_preds
                , average = "weighted"
            )

            val_acc = accuracy_score(running_labels, running_preds)
            val_precision = precision_score(running_labels, running_preds, average="weighted", zero_division=0)
            val_recall = recall_score(running_labels, running_preds, average="weighted", zero_division=0)
            val_f1 = f1_score(running_labels, running_preds, average="weighted", zero_division=0)





In [ ]:
def set_seed(seed):
    # Python's built-in random
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)

    if torch.cuda.is_available():
        torch.cuda.manual_seed(seed)
        torch.cuda.manual_seed_all(seed)

In [ ]:
test_f1s = []
test_accs = []
test_precisions = []
test_recalls = []
test_aucs = []

for seed in range(0, 10):
  config = {
      "is_multilabel":False,
      "device_ids": [0],
  }

  set_seed(seed)


  # ---- Stratified splitting ----
  all_indices = list(range(len(X)))
  all_labels = y  # label_idx for each sample

  # First split: train+val (90%) vs test (10%)
  trainval_indices, test_indices = train_test_split(
      all_indices,
      test_size=0.1,
      random_state=seed,
      stratify=all_labels
  )

  trainval_labels = [all_labels[i] for i in trainval_indices]

  # Second split: train (90% of trainval) vs val (10% of trainval)
  train_indices, val_indices = train_test_split(
      trainval_indices,
      test_size=0.1,
      random_state=seed,
      stratify=trainval_labels
  )

  # Create datasets
  train_ds = TensorDataset(torch.Tensor(X[train_indices]), torch.Tensor(y[train_indices]))
  val_ds = TensorDataset(torch.Tensor(X[val_indices]), torch.Tensor(y[val_indices]))
  test_ds = TensorDataset(torch.Tensor(X[test_indices]), torch.Tensor(y[test_indices]))

  train_loader = DataLoader(train_ds, batch_size=32, shuffle=True, drop_last=True)
  val_loader = DataLoader(val_ds, batch_size=32, shuffle=False)
  test_loader = DataLoader(test_ds, batch_size=32, shuffle=False)

  config = {
      "is_multilabel":False,
      "device_ids": [0],
  }

  train_loaders = {
      "train": train_loader,
      "val": val_loader,
      "test": test_loader
  }


  model = LightX3ECG(
      num_classes = 11,
  )

  # if not config["is_multilabel"]:
  criterion = F.cross_entropy
  # else:
  # criterion = F.binary_cross_entropy_with_logits

  optimizer = optim.Adam(
      model.parameters(),
      lr = 1e-6, weight_decay = 5e-5,
  )

  scheduler = optim.lr_scheduler.CosineAnnealingLR(
      optimizer,
      eta_min = 1e-4, T_max = 20,
  )

  train_fn(
      train_loaders,
      model,
      num_epochs = 20,
      config = config,
      criterion = criterion,
      optimizer = optimizer,
      scheduler = scheduler,
  )


  # Validation
  with torch.no_grad():
      model.eval()
      running_loss = 0.0
      running_labels, running_preds, running_probs = [], [], []
      for ecgs, labels in tqdm(test_loader):
          ecgs, labels = ecgs.cuda(), labels.cuda()

          logits = model(ecgs)
          loss = criterion(logits, labels)
          probs = torch.softmax(logits, dim=1).cpu().numpy()
          running_loss = running_loss + loss.item()*ecgs.size(0)
          labels, preds = list(labels.data.cpu().numpy()), list(torch.max(logits, 1)[1].detach().cpu().numpy()) if not config["is_multilabel"] else list(np.where(torch.sigmoid(logits).detach().cpu().numpy() >= 0.50, 1, 0))
          running_labels.extend(labels), running_preds.extend(preds), running_probs.extend(probs)

      test_epoch_loss, test_epoch_f1 = running_loss/len(test_loader.dataset), f1_score(
          running_labels, running_preds
          , average = "weighted"
      )

      test_acc = accuracy_score(running_labels, running_preds)
      test_precision = precision_score(running_labels, running_preds, average="weighted", zero_division=0)
      test_recall = recall_score(running_labels, running_preds, average="weighted", zero_division=0)
      test_f1 = f1_score(running_labels, running_preds, average="weighted", zero_division=0)
      # Some classes may be missing in a split, handle safely
      try:
        y_true = np.eye(11)[running_labels]
        y_score = np.array(running_probs)

        auc_list = []
        for i in range(11):
            if np.any(y_true[:, i]):  # class i exists
                auc_list.append(roc_auc_score(y_true[:, i], y_score[:, i]))
        if auc_list:
            auc = np.mean(auc_list)
        else:
            auc = float("nan")
      except ValueError:
          auc = float("nan")

      print("{:<5}, f1:{:.4f}, precision:{:.4f}, recall:{:.4f}, accuracy:{:.4f},".format(
                  "eval",
                  test_f1, test_precision, test_recall, test_acc
              ))

      test_accs.append(test_acc)
      test_precisions.append(test_precision)
      test_recalls.append(test_recall)
      test_f1s.append(test_f1)
      test_aucs.append(auc)

print(test_accs)
print(test_precisions)
print(test_recalls)
print(test_f1s)
print(test_aucs)


Start Training ...
 =  =  =  =  =  =  =  =  =  =  =  =  =  =  =  = 


  0%|          | 0/558 [00:00<?, ?it/s]

  0%|          | 0/63 [00:00<?, ?it/s]

  0%|          | 0/558 [00:00<?, ?it/s]

  0%|          | 0/63 [00:00<?, ?it/s]

...

  0%|          | 0/63 [00:00<?, ?it/s]

  0%|          | 0/558 [00:00<?, ?it/s]

  0%|          | 0/63 [00:00<?, ?it/s]

  0%|          | 0/69 [00:00<?, ?it/s]

eval , f1:0.8059, precision:0.8098, recall:0.8154, accuracy:0.8154,
[0.81859410430839, 0.7972789115646258, 0.8276643990929705, 0.8276643990929705, 0.817687074829932, 0.1287981859410431, 0.7755102040816326, 0.7401360544217687, 0.8263038548752835, 0.8154195011337868]
[0.8086648540797945, 0.8124770703411192, 0.8179842507063245, 0.8208455480856595, 0.8123109285691925, 0.7707666959632975, 0.7784745196935234, 0.7714425035832322, 0.8303761780969235, 0.8097594158986879]
[0.81859410430839, 0.7972789115646258, 0.8276643990929705, 0.8276643990929705, 0.817687074829932, 0.1287981859410431, 0.7755102040816326, 0.7401360544217687, 0.8263038548752835, 0.8154195011337868]
[0.8023857026718665, 0.7923775549260157, 0.8202582244277311, 0.8175574402100162, 0.7996985406362208, 0.045040047347483736, 0.7570630815509727, 0.732678672522158, 0.8094889045814351, 0.8058693836963434]
[0.9149998233545645, 0.8989908222237207, 0.9038309382933043, 0.9031868204302569, 0.8685893999501109, 0.7613173248320713, 0.9174804145

In [ ]:
test_f1s, test_accs,test_precisions,test_recalls,test_aucs


([], [], [], [], [])

In [5]:
!pip install torchinfo

In [6]:
from torchinfo import summary

model = LightX3ECG(
    num_classes = 11,
)

summary(model, (1, 12, 5000))

Layer (type:depth-idx)                                  Output Shape              Param #
LightX3ECG                                              [1, 11]                   --
├─LightSEResNet18: 1-1                                  [1, 512, 1]               --
│    └─Sequential: 2-1                                  [1, 64, 1250]             --
│    │    └─Conv1d: 3-1                                 [1, 64, 2500]             1,024
│    │    └─BatchNorm1d: 3-2                            [1, 64, 2500]             128
│    │    └─ReLU: 3-3                                   [1, 64, 2500]             --
│    │    └─MaxPool1d: 3-4                              [1, 64, 1250]             --
│    └─Sequential: 2-2                                  [1, 64, 1250]             --
│    │    └─LightSEResBlock: 3-5                        [1, 64, 1250]             9,924
│    │    └─LightSEResBlock: 3-6                        [1, 64, 1250]             9,924
│    └─Sequential: 2-3                            

In [ ]:
from sklearn.model_selection import train_test_split
from torch.utils.data import TensorDataset, DataLoader

# ---- Stratified splitting ----
all_indices = list(range(len(X)))
all_labels = y  # label_idx for each sample

# First split: train+val (90%) vs test (10%)
trainval_indices, test_indices = train_test_split(
    all_indices,
    test_size=0.1,
    random_state=10,
    stratify=all_labels
)

trainval_labels = [all_labels[i] for i in trainval_indices]

# Second split: train (90% of trainval) vs val (10% of trainval)
train_indices, val_indices = train_test_split(
    trainval_indices,
    test_size=0.1,
    random_state=10,
    stratify=trainval_labels
)

print(np.array(X).shape, np.array(Y).shape)

# Create datasets
train_ds = TensorDataset(torch.Tensor(X[train_indices]), torch.Tensor(y[train_indices]))
val_ds = TensorDataset(torch.Tensor(X[val_indices]), torch.Tensor(y[val_indices]))
test_ds = TensorDataset(torch.Tensor(X[test_indices]), torch.Tensor(y[test_indices]))

train_loader = DataLoader(train_ds, batch_size=32, shuffle=True, drop_last=True)
val_loader = DataLoader(val_ds, batch_size=32, shuffle=False)
test_loader = DataLoader(test_ds, batch_size=32, shuffle=False)

config = {

    "is_multilabel":False,
    "device_ids": [0],
}

train_loaders = {
    "train": train_loader,
    "val": val_loader,
    "test": test_loader
}



# Validation
with torch.no_grad():
    model.eval()
    running_loss = 0.0
    running_labels, running_preds = [], []
    for ecgs, labels in tqdm(test_loader):
        ecgs, labels = ecgs.cuda(), labels.cuda()

        logits = model(ecgs)
        loss = criterion(logits, labels)

        running_loss = running_loss + loss.item()*ecgs.size(0)
        labels, preds = list(labels.data.cpu().numpy()), list(torch.max(logits, 1)[1].detach().cpu().numpy()) if not config["is_multilabel"] else list(np.where(torch.sigmoid(logits).detach().cpu().numpy() >= 0.50, 1, 0))
        running_labels.extend(labels), running_preds.extend(preds)

    test_epoch_loss, test_epoch_f1 = running_loss/len(test_loader.dataset), f1_score(
        running_labels, running_preds
        , average = "weighted"
    )

    test_acc = accuracy_score(running_labels, running_preds)
    test_precision = precision_score(running_labels, running_preds, average="weighted", zero_division=0)
    test_recall = recall_score(running_labels, running_preds, average="weighted", zero_division=0)
    test_f1 = f1_score(running_labels, running_preds, average="weighted", zero_division=0)

    print("{:<5}, f1:{:.4f}, precision:{:.4f}, recall:{:.4f}, accuracy:{:.4f},".format(
                "eval",
                test_f1, test_precision, test_recall, test_acc
            ))


  0%|          | 0/69 [00:00<?, ?it/s]

eval , f1:0.8388, precision:0.8372, recall:0.8458, accuracy:0.8458,


In [ ]:
pip install torchinfo